<a href="https://colab.research.google.com/github/gwisnu/mapping-pemilu2019/blob/master/mapping-pemilu2019.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
import folium
import json 
import urllib
import requests
import pandas as pd
from pandas.io.json import json_normalize
import datetime

In [0]:
import time
timestamp = int(time.time())
#print(timestamp)

In [0]:
url ='https://kawal-c1.appspot.com/api/c/0?'+str(timestamp)
kpu = 'https://pemilu2019.kpu.go.id/static/json/hhcw/ppwp.json'
response = requests.get(url ,verify=False)
data = json.loads(response.text)

/usr/local/lib/python3.6/dist-packages/urllib3/connectionpool.py:847: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)


In [0]:
table = list()
row ={}
for i in (data['data']):
    flatten_json = json_normalize(data['data'][i],errors='ignore')
    #print (i, (normal.iloc[0]['sum.pas1']), normal.iloc[0]['sum.pas2'], normal.iloc[0]['sum.error'])
    row.update(row)
    table.append({"code":i,"paslon01":(flatten_json.iloc[0]['sum.pas1']),"paslon02":(flatten_json.iloc[0]['sum.pas2']),"sah":(flatten_json.iloc[0]['sum.sah'])})

In [0]:
df=pd.DataFrame(table)
df["code"] = pd.to_numeric(df["code"])
df.head()
df['persen01'] = (df['paslon01'] / (df['paslon01'] + df['paslon02'])) * 100
df['persen02'] = (df['paslon02'] / (df['paslon01'] + df['paslon02'])) * 100
df.dtypes

code          int64
paslon01      int64
paslon02      int64
sah           int64
persen01    float64
persen02    float64
dtype: object

In [0]:
indo_geo ='https://github.com/gwisnu/geojson/blob/master/province.geojson?raw=true'
indo = 'https://github.com/gwisnu/geojson/raw/master/province.geojson'
m = folium.Map(
    location=[-2, 117],
    tiles='cartodbpositron',
    zoom_start=5
)

#bins = list(df['persen01'].quantile([0, 0.25, 0.5, 0.75, 1]))
bins = [0, 12.5, 25,37.5, 50,62.5, 75, 87.5, 100]
folium.Choropleth(
    geo_data=indo,
    data=df,
    name = 'paslon01',
    columns=['code', 'persen01'],
    key_on='feature.properties.code',
    fill_color='RdYlGn',
    fill_opacity=0.7,
    line_opacity=0.5,
    bins=bins,
    reset=True
).add_to(m)
bins = [0, 12.5, 25,37.5, 50,62.5, 75, 87.5, 100]
folium.Choropleth(
    geo_data=indo,
    data=df,
    name = 'paslon02',
    columns=['code', 'persen02'],
    key_on='feature.properties.code',
    fill_color='RdYlGn',
    fill_opacity=0.7,
    line_opacity=0.5,
    bins=bins,
    reset=True
).add_to(m)

folium.LayerControl().add_to(m)
m